In [ ]:
!pip install mapclassify

In [ ]:
from pathlib import Path
from zipfile import ZipFile
import geopandas as gpd
import pandas as pd
import plotly.express as px
import folium
import panel as pn
from shapely.geometry import Polygon, Point
import math
from typing import List
import itertools
pn.extension('plotly', sizing_mode="stretch_width")

## ファイルの読み込みもこけることがある

In [ ]:
# パスをコピペして貼り付け、プリント
a_path = '/content/drive/MyDrive/od-book/国勢調査/A002005212020DDSWC27.zip'
t_path = '/content/drive/MyDrive/od-book/国勢調査/tblT001082C27.zip'
# Pathオブジェクトにして、変数に渡す
toukei_zip_path = Path(t_path)
kyokai_zip_path = Path(a_path)

# CSVファイルの読み込み 失敗する
toukei_df = pd.read_csv(toukei_zip_path)

UnicodeDecodeError: ignored

In [ ]:
# encodingにcp932を指定しないといけない
toukei_df = pd.read_csv(toukei_zip_path, encoding='cp932')
toukei_df.head()

KEY_CODE  HYOSYO CITYNAME   NAME  HTKSYORI  HTKSAKI GASSAN  \
0           NaN     NaN      NaN    NaN       NaN      NaN    NaN   
1  2.710200e+04     1.0   大阪市都島区    NaN       0.0      NaN    NaN   
2  2.710200e+08     3.0   大阪市都島区     片町       0.0      NaN    NaN   
3  2.710200e+10     4.0   大阪市都島区  片町一丁目       0.0      NaN    NaN   
4  2.710200e+10     4.0   大阪市都島区  片町二丁目       0.0      NaN    NaN   

    T001082001 T001082002 T001082003  ... T001082051 T001082052 T001082053  \
0  総数、年齢「不詳」含む     総数０～４歳     総数５～９歳  ...    女４５～４９歳    女５０～５４歳    女５５～５９歳   
1       107904       3785       4069  ...       4238       3643       3243   
2         2408         67         30  ...         84         66         49   
3         1562         47         27  ...         59         49         34   
4          846         20          3  ...         25         17         15   

  T001082054 T001082055 T001082056 T001082057 T001082058 T001082059 T001082060  
0    女６０～６４歳    女６５～６９歳    女７０～７４歳     女１５歳未満    女１５～６４歳     女６５歳以上     女７５歳以上  
1       3012       3119       3413       5743      33518      14421       7889  
2         38         33         41         49        833        125         51  
3         27         22         24         38        554         74         28  
4         11         11         17         11        279         51         23  

[5 rows x 67 columns]

## ビッグデータを観察する手段を知る

- ビッグデータを扱うためのツール選定
- 書籍で扱うデータ
- 各地域の年齢別人口（５歳刻み、男女合計・別）


In [ ]:
data_path ='/content/drive/MyDrive/od-book/国勢調査/kokusei_osaka.gpkg'
data = gpd.read_file(data_path)
print(data.shape)
print(data.info())

(8729, 69)
<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 8729 entries, 0 to 8728
Data columns (total 69 columns):
 #   Column             Non-Null Count  Dtype   
---  ------             --------------  -----   
 0   KEY_CODE           8729 non-null   int64   
 1   area               8729 non-null   float64 
 2   HYOSYO             8729 non-null   int64   
 3   CITYNAME           8729 non-null   object  
 4   NAME               8725 non-null   object  
 5   HTKSYORI           8729 non-null   int64   
 6   HTKSAKI            192 non-null    float64 
 7   GASSAN             135 non-null    object  
 8   total_all          8729 non-null   int64   
 9   total_0_4_age      8729 non-null   int64   
 10  total_5_9_age      8729 non-null   int64   
 11  total_10_14_age    8729 non-null   int64   
 12  total_15_19_age    8729 non-null   int64   
 13  total_20_24_age    8729 non-null   int64   
 14  total_25_29_age    8729 non-null   int64   
 15  total_30_34_age    8729 non-null   i

In [ ]:
data = data.drop(['KEY_CODE', 'HYOSYO', 'NAME', 'HTKSYORI', 'HTKSAKI', 'GASSAN'], axis=1)
cityname = data.dissolve('CITYNAME', aggfunc='sum', as_index=False) # ①
for col in cityname.columns[cityname.columns.get_loc('total_all'):]: # ②
    cityname[col] = cityname[col].astype(int)
ratio = cityname.loc[:, 'area':].apply(lambda x: x/cityname['total_all'] if not x.name == 'area' else cityname['total_all']/ x)
ratio = ratio.drop('total_all', axis=1) #①
cols = [f'ratio_{col}' for col in ratio.columns] #②
ratio.columns = cols
cityname = pd.merge(cityname, ratio, left_index=True, right_index=True) #③

# 詳細にデータを見る


In [ ]:
fig = px.scatter(cityname, # ①
                 x='ratio_total_15_age_less', # ②
                 y='ratio_total_65_age_over',
                 color='ratio_total_15_64_age', # ③
                 size='ratio_area', # ④
                 hover_data=['CITYNAME'], # ⑤
                 marginal_x='violin', # ⑥
                 marginal_y='violin',
                 trendline='ols', # ⑦
                 title='年齢別人口比率と人口密度'
                 )
fig.show()


# より多くのデータを容易に観察するためにツールを使う

In [ ]:
cols_list = list(cityname.columns[3:].values)

def show_chart(df, col1, col2, col3):
    fig = px.scatter(
        df,
        x=col1,
        y=col2,
        color=col3,
        size='ratio_area',
        hover_data=['CITYNAME'],
        marginal_x='violin',
        marginal_y='violin',
        trendline='ols',
        title=f'年齢別人口比率と人口密度 X:{col1}, Y:{col2}, Color: {col3}'
    )
    return fig

col1 = pn.widgets.Select(name='col1', options=cols_list, value=cols_list[1])
col2 = pn.widgets.Select(name='col2', options=cols_list, value=cols_list[1])
col3 = pn.widgets.Select(name='color', options=cols_list, value=cols_list[1])
interactive_chart = pn.bind(show_chart, cityname, col1, col2, col3)
pn.Column(
    pn.Row(col1, col2),
    col3,
    interactive_chart
)

Column(sizing_mode='stretch_width')
    [0] Row(sizing_mode='stretch_width')
        [0] Select(name='col1', options=['total_all', ...], sizing_mode='stretch_width', value='total_0_4_age')
        [1] Select(name='col2', options=['total_all', ...], sizing_mode='stretch_width', value='total_0_4_age')
    [1] Select(name='color', options=['total_all', ...], sizing_mode='stretch_width', value='total_0_4_age')
    [2] ParamFunction(function, _pane=Plotly, defer_load=False, sizing_mode='stretch_width')

In [ ]:
# 選択肢をデータのカラムから作成。今回は広さも観察したいので'area'を含む
cols_list = list(cityname.columns[2:].values)

# 棒グラフを作成する関数
def show_chart(col_name):
    fig = px.bar(cityname.sort_values(col_name),
                 x='CITYNAME',
                 y=col_name,
                 title=f'CITYNAME別: {col_name}',
                 height=600
                 )
    return fig

# 地図を作成する関数
def show_map(col_name):
    tooltip=['CITYNAME', 'total_all'] + [col_name]
    map = cityname.explore(col_name, tooltip=tooltip, height=600) #①
    map = pn.pane.plot.Folium(map, height=600) #②
    return map

# 表示データを選択するSelect
col_sel = pn.widgets.Select(name='dsel', options=cols_list)

# グラフ、地図共に上のSelectをバインド
interactive_chart = pn.bind(show_chart, col_sel)
interactive_map = pn.bind(show_map, col_sel)

# 地図とグラフが横に並ぶようにレイアウトを作成
pn.Column(
    col_sel,
    pn.Row(
        interactive_map, interactive_chart
    )
)


Column(sizing_mode='stretch_width')
    [0] Select(name='dsel', options=['area', 'total_all', ...], sizing_mode='stretch_width', value='area')
    [1] Row(sizing_mode='stretch_width')
        [0] ParamFunction(function, _pane=Folium, defer_load=False, sizing_mode='stretch_width')
        [1] ParamFunction(function, _pane=Plotly, defer_load=False, sizing_mode='stretch_width')

## オリジナル商圏を作成
- 自社の狙う年齢層が多そうかつ、勝負できそうなマーケットを探す

In [ ]:
data_path = '/content/drive/MyDrive/od-book/国勢調査/kokusei_osaka_add_new_class.gpkg'
data = gpd.read_file(data_path)

# 大阪を囲む場所にポイントを作る
data6674 = data.to_crs('EPSG:6674')
osaka_poly6674 = data6674.unary_union
minx, miny, maxx, maxy = osaka_poly6674.bounds
minx, miny, maxx, maxy = math.ceil(minx), math.ceil(miny), math.floor(maxx), math.floor(maxy)
geo_list = list()
for x in range(minx, maxx, 5000):
    for y in range(miny, maxy, 5000):
        geo_list.append(Point(x, y))

point_data = gpd.GeoDataFrame(geometry=geo_list) # ⓵
point_data = point_data.set_crs('EPSG:6674') # ②
point_data['intersects'] = point_data['geometry'].map(lambda x: x.intersects(osaka_poly6674))
point_data = point_data.query('intersects == True').reset_index(drop=True)
point_data['geometry'] = point_data['geometry'].map(lambda x: x.buffer(5000)) #①
point_data = point_data.to_crs('EPSG:4326')
point_data['name'] = point_data.index.map(lambda x: f'point_{x:02}') # ポイントに名前を付ける

## 作成した5km商圏を可視化する
osaka_poly = data.unary_union
center = point_data.unary_union.centroid

m = folium.Map([center.y, center.x])
folium.GeoJson(point_data).add_to(m)
folium.GeoJson(osaka_poly,
               style_function=lambda feature: {
               'color': 'red'  # 線色を赤色に指定
                }
               ).add_to(m)
m

In [ ]:
def calc_shoken(geo_polygon: Polygon, data: gpd.GeoDataFrame) -> gpd.GeoDataFrame: #①
    '''
    geo_polygonに重なる地域のデータを抽出して返す
    '''
    cols = ['CITYNAME', 'area', 'geometry'] #②
    cols += [col for col in data.columns if col.startswith('total')] #②
    data1 = data[cols].copy() # 必要列を抽出したデータを作成 #③
    data1['tf'] = data1['geometry'].map(lambda x: geo_polygon.intersects(x)) #④
    data1 = data1.query('tf == True') #⑤
    return data1


point_dict = dict() #⑥
for i in point_data.index: #⑦
    name = point_data.loc[i, 'name'] #⑧
    geo = point_data.loc[i, 'geometry'] #⑨
    t_data = calc_shoken(geo, data) #⑩
    point_dict[name] = t_data #⑪

point_sum = list() #①
for k, v in point_dict.items(): #②
    cols = [col for col in v.columns if col.startswith('total')] #③
    d1 = v[cols].sum() #④
    d1.name = k #⑤
    point_sum.append(d1) #⑥

point_sum_df = pd.concat(point_sum, axis=1) #⑦
point_ratio_df = point_sum_df / point_sum_df.loc['total_all'] # ⓵
point_ratio_df.index = [f'ratio_{col}' for col in point_ratio_df.index] # ②
conc_points = pd.concat([point_sum_df, point_ratio_df]).T

conc_desc = conc_points.describe(percentiles=[i/10 for i in range(0, 10)]) # ⓵
conc_desc50 = conc_desc.loc['50%', 'total_all'] # ②
conc_desc70 = conc_desc.loc['70%', 'total_all'] # ③
conc_points56 = conc_points.query('total_all > @conc_desc50 and total_all < @conc_desc70').copy() #④
conc_points56 = conc_points56.sort_values('ratio_total_45_49_age', ascending=False) # ⑤
head_conc_points56 = conc_points56.head() # ⑥
point_data = point_data.set_index('name') # ⑦
head_conc_points56_with_geo = pd.merge(point_data, head_conc_points56, left_index=True, right_index=True) # ⑧
head_conc_points56_with_geo.explore('total_45_49_age', tooltip=['total_45_49_age', 'ratio_total_45_49_age']) #⑨